In [1]:
# Importing gensim summarize
from gensim.summarization import summarize

# Import Relevant Summarizers, Parsers and Tokenizers from sumy
import sumy
from sumy.parsers.plaintext import PlaintextParser
from sumy.parsers.html import HtmlParser
from sumy.nlp.tokenizers import Tokenizer
from sumy.summarizers.lex_rank import LexRankSummarizer
from sumy.summarizers.luhn import LuhnSummarizer
from sumy.summarizers.lsa import LsaSummarizer
from sumy.summarizers.lsa import LsaSummarizer as Lsa
from sumy.summarizers.luhn import LuhnSummarizer as Luhn
from sumy.summarizers.text_rank import TextRankSummarizer as TxtRank
from sumy.summarizers.lex_rank import LexRankSummarizer as LexRank
from sumy.summarizers.sum_basic import SumBasicSummarizer as SumBasic
from sumy.summarizers.kl import KLSummarizer as KL
from sumy.summarizers.edmundson import EdmundsonSummarizer as Edmundson
from sumy.nlp.stemmers import Stemmer
from sumy.utils import get_stop_words

In [2]:
# Importing Basic Python Libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

import math # Importing math

# Abstract Syntax Trees
import ast

# tqdm for progress 
from tqdm import tqdm

# time
from time import time

In [3]:
# Importing Overall Summary
dv_summ=pd.read_csv('devopedia/devopedia/spiders/overall_summary.csv')

# Importing articles_152.csv
articles=pd.read_csv('devopedia/devopedia/spiders/articles_152.csv')

There is an article on "Dotdot" which actually has No Reference links. So the filename column there is actually labelled as "No References". 
https://devopedia.org/dotdot

So here we will change the No References to "" below

In [4]:
articles.loc[(articles.file_name=="No References"),'file_name']=""

In [5]:
articles[articles.title=="Dotdot"]

title                                            summary  \
75  Dotdot   is the universal language of the Internet of ...   

                                                   QA references file_name  
75  [{'question': "What's the need to have Dotdot?...         []

In [6]:
articles.file_name.head()

0                         MQTT_ref.csv
1    Race Condition (Software)_ref.csv
2                       HTTP-2_ref.csv
3                        Li-Fi_ref.csv
4               Web Annotation_ref.csv
Name: file_name, dtype: object

In [7]:
# Changing overall_summary colname to devopedia_summary for easy clarity

dv_summ.rename(columns={'overall_summary':'devopedia_summary'},inplace=True)

In [8]:
LANGUAGE="english"
def summarisation(text,ratio=0.1,summary_type='gensim'):   
    try:
        stemmer = Stemmer(LANGUAGE)
        parser = PlaintextParser.from_string(text,Tokenizer(LANGUAGE))
        # Setting number of sentences inside summary as 10% of document
        # or whatever ratio we call the function with
        SENTENCES_COUNT=len(parser.document.sentences)*ratio
        if summary_type=='gensim':
            return summarize(text,ratio)
        elif summary_type=='lsa':
            lsaSummarizer = Lsa(stemmer)
            lsaSummarizer.stop_words = get_stop_words(LANGUAGE)
            return "".join([str(sent) for sent in \
                            lsaSummarizer(parser.document, SENTENCES_COUNT)])
        elif summary_type=='lsa_stemmer':
            summarizer_lsa2 = LsaSummarizer(Stemmer(LANGUAGE))
            summarizer_lsa2.stop_words = get_stop_words(LANGUAGE)
            return "".join([str(sent) for sent in \
                            summarizer_lsa2(parser.document,SENTENCES_COUNT)])
        elif summary_type=='luhn':
            luhnSummarizer = Luhn(stemmer)
            luhnSummarizer.stop_words = get_stop_words(LANGUAGE)
            return "".join([str(sent) for sent in \
                            luhnSummarizer(parser.document, SENTENCES_COUNT)])
        elif summary_type=='lexrank':
            lexrankSummarizer = LexRank(stemmer)
            lexrankSummarizer.stop_words = get_stop_words(LANGUAGE)
            return "".join([str(sent) for sent in \
                            lexrankSummarizer(parser.document, SENTENCES_COUNT)])
        elif summary_type=='textrank':
            textrankSummarizer = TxtRank(stemmer)
            textrankSummarizer.stop_words = get_stop_words(LANGUAGE)
            return "".join([str(sent) for sent in \
                            textrankSummarizer(parser.document, SENTENCES_COUNT)])
        elif summary_type=='sumbasic':
            sumbasicSummarizer = SumBasic(stemmer)
            sumbasicSummarizer.stop_words = get_stop_words(LANGUAGE)
            return "".join([str(sent) for sent in \
                            sumbasicSummarizer(parser.document, SENTENCES_COUNT)])
        elif summary_type=='kldiv':
            klSummarizer = KL(stemmer)
            klSummarizer.stop_words = get_stop_words(LANGUAGE)
            return "".join([str(sent) for sent in \
                            klSummarizer(parser.document, SENTENCES_COUNT)])
    except:
        return ""


In [9]:
articles.file_name.head()

0                         MQTT_ref.csv
1    Race Condition (Software)_ref.csv
2                       HTTP-2_ref.csv
3                        Li-Fi_ref.csv
4               Web Annotation_ref.csv
Name: file_name, dtype: object

In [10]:
# Creating a filter for our selected articles since db is too large for CPU
mask=(articles.file_name=="MQTT_ref.csv") | \
(articles.file_name=="Text Summarization_ref.csv") | \
(articles.file_name=="Data Science_ref.csv") | \
(articles.file_name=="Deep Learning Frameworks_ref.csv") | \
(articles.file_name=='Decision Trees for Machine Learning_ref.csv')

In [11]:
articles_trunc=articles[mask]
articles_trunc.shape

(5, 5)

In [14]:
%%time

# Making list of summary types
# here we are ommitting KL Sum due to computational reasons i.e. time taken
summary_types=["gensim",'lsa','lsa_stemmer','luhn','lexrank','sumbasic']

print("Begin")

# Creating dfs......
article_df=pd.DataFrame(columns=['title','reference_link','file_name','text',\
                                 'summary','summary_type'])
final_df=pd.DataFrame(columns=['title','final_summary','summary_type'])

for summary_type in summary_types:
    print("Starting "+summary_type+" summarisation")
    for index,row in tqdm(articles_trunc.iterrows()):
        #print("\n\n"+row['title'])
        # If filename missing or the filename column is "" 
        if ( not isinstance(row['file_name'],str) )or \
            "reference" in str(row['file_name']).lower():
            print("continue")
            continue
        # Reading the _cleaned.csv filenames iteratively
        # 'devopedia/devopedia/spiders/'+'_cleaned.csv'
        text=pd.read_csv('devopedia/devopedia/spiders/'+row['file_name'][:-4]+\
                         "_cleaned.csv")
        text=text.replace(np.nan,"",regex=True)
        concat_summary='' # Initialzing summary variable
        # Iterating over each _cleaned.csv file df, using iterrows
        for i,r in text.iterrows():
            s=str(summarisation(r['text'],ratio=0.15,summary_type=summary_type))
            print(s)
            row_dict={}
            row_dict['title']=row['title']
            row_dict['reference_link']=r['reference_link']
            row_dict['file_name']=row['file_name']
            row_dict['text']=r['text']
            row_dict['summary']=s
            row_dict['summary_type']=summary_type
            article_df=article_df.append(row_dict,ignore_index=True)
            concat_summary=concat_summary+s

        # Creating Summary of Individual Reference Summaries with 15% ratio
        final_sum=summarisation(concat_summary,ratio=.15,\
                                summary_type=summary_type)
        row_dict={}
        row_dict['title']=row['title']
        row_dict['summary_type']=summary_type
        row_dict['final_summary']=final_sum
        final_df=final_df.append(row_dict,ignore_index=True)
        article_df.to_csv("article_level_summary_output_trunc.csv",index=False)
        final_df.to_csv("final_summary_output_trunc.csv",index=False)

0it [00:00, ?it/s]

Begin
Starting gensim summarisation
Abstract:  MQTT is a Client Server publish/subscribe messaging transport protocol.
Others should send comments to the TC’s public comment list, after subscribing to it by following the instructions at the “Send A Comment” button on the TC’s web page at https://www.oasis-open.org/committees/mqtt/.
For information on whether any patents have been disclosed that may be essential to implementing this specification, and any offers of patent licensing terms, please refer to the Intellectual Property Rights section of the Technical Committee web page (https://www.oasis-open.org/committees/mqtt/ipr.php).
29 October 2014 Page 8 of 81  \x0c1  2  3  4  5  6  7  8  9  10  11  12 13 14  15  16  17 18  1  Introduction  1.1  Organization of MQTT   This specification is split into seven chapters:    Chapter 1 - Introduction    Chapter 2 - MQTT Control Packet format    Chapter 3 - MQTT Control Packets    Chapter 4 - Operational behavior    Chapter 5 - Security    Cha

Abstract:  MQTT is a Client Server publish/subscribe messaging transport protocol.
For information on whether any patents have been disclosed that may be essential to implementing this specification, and any offers of patent licensing terms, please refer to the Intellectual Property Rights section of the TC’s web page (https://www.oasis-open.org/committees/mqtt/ipr.php).
For information on whether any patents have been disclosed that may be essential to implementing this specification, and any offers of patent licensing terms, please refer to the Intellectual Property Rights section of the TC’s web page (https://www.oasis-open.org/committees/mqtt/ipr.php).
When an Application Message is transported by MQTT it contains payload data, a Quality of Service (QoS), a collection of Properties, and a Topic Name.
07 March 2019 Page 11 of 137  \x0c42  43  44 45  46 47 48 49 50  51  52  53 54  55  56  57 58 59  60  61  62 63 64 65 66  67  68  69 70 71  72  73  74 75  76  77  78 79  80  81  82 83 

Slideshare uses cookies to improve functionality and performance, and to provide you with relevant advertising.
Slideshare uses cookies to improve functionality and performance, and to provide you with relevant advertising.
We use your LinkedIn profile and activity data to personalize ads and to show you more relevant ads.
MQTT - MQ Telemetry Transport for M...
A Short Report on MQTT protocol for...
In today’s mobile world, the volume of connected devices and data is growing at a rapid pace.
As more and more “things” become part of the Internet (refrigerators, pacemakers, cows?), the importance of scalable, reliable and efficient messaging becomes paramount.
In this talk we will dive into MQTT: a lightweight, open standard publish/subscribe protocol for rapid messaging between “things”.
MQTT is simple to understand, yet robust enough to support interactions between millions of devices and users.
MQTT is being used in connected car applications, mobile banking, Facebook Messenger, and m

The Massively Scalable MQTT Broker for IoT and Mobile Applications
EMQ (Erlang MQTT Broker) is a distributed, massively scalable, highly extensible MQTT message broker written in Erlang/OTP.
The integration of MQTT Brokers in Online BusinessesEvery day new technology trends are having a great impact on the gambling industry, especially in online casinos.
When it comes to the online business and online casinos, the MQTT open source Broker is the one that manages the entire data of the transmission system of all casino applications, including roulette games, blackjack games, bingo or poker games-- and it doesn't matter if it is a mobile, web or desktop app.
EMQ provides a scalable, enterprise grade, extensible open-source MQTT broker for IoT, M2M, Smart Hardware, Mobile Messaging and HTML5 Web Messaging Applications.
Sensors, Mobiles, Browsers and Application Servers can be connected by EMQ brokers with asynchronous MQTT messages.
The Massively Scalable MQTT Broker powering your IoT, M2M

...

(2014).Inourapproach,thedecoder-vocabularyofeachmini-batchisre-strictedtowordsinthesourcedocumentsofthatbatch.Inaddition,themostfrequentwordsinthetargetdictionaryareaddeduntilthevocabularyreachesaﬁxedsize.Theaimofthistechniqueistoreducethesizeofthesoft-maxlayerofthedecoderwhichisthemaincomputationalbottle-neck.Inaddition,thistechniquealsospeedsupconvergencebyfocusingthemodelingeffortonlyonthewordsthatareessentialtoagivenexample.Thistechniqueisparticularlywellsuitedtosum-marizationsincealargeproportionofthewordsinthesummarycomefromthesourcedocumentinanycase.2.2CapturingKeywordsusingFeature-richEncoderInsummarization,oneofthekeychallengesistoidentifythekeyconceptsandkeyentitiesinthedocument,aroundwhichthestoryrevolves.Inordertoaccomplishthisgoal,wemayneedtogobeyondtheword-embeddings-basedrepresen-tationoftheinputdocumentandcaptureaddi-tionallinguisticfeaturessuchasparts-of-speechtags,named-entitytags,andTFandIDFstatis-ticsofthewords.Wethereforecreateadditionallook-upbasedembeddingmatrice

Could I lean on Natural Language Processing (NLP) techniques to help me out?Note: This article requires a basic understanding of a few deep learning concepts.I recommend going through the below articles.How does the Attention Mechanism Work?However, I encourage you to go through it because it will give you a solid idea of this awesome NLP concept.What is Text Summarization in NLP?Let’s first understand what text summarization is before we look at how it works.Extractive Summarization The name gives away what this approach does.Those extracted sentences would be our summary.This includes Sentiment classification, Neural Machine Translation, and Named Entity Recognition – some very common applications of sequential information.So, we can model this as a Many-to-Many Seq2Seq problem.The input is a long sequence of words and the output will be a short version of the input sequence.Let us see in detail on how to set up the encoder and decoder.Remember, this is because the encoder and decode

(b)Anetworkdiagramfortheattention-basedencoderenc3.Theparametersareθ=(E,U,V,W)whereE∈RD×Visawordembeddingmatrix,U∈R(CD)×H,V∈RV×H,W∈RV×Hareweightmatrices,4Disthesizeofthewordembeddings,andhisahiddenlayerofsizeH.Theblack-boxfunctionencisacontextualencodertermthatre-turnsavectorofsizeHrepresentingtheinputandcurrentcontext;weconsiderseveralpossiblevari-ants,describedsubsequently.Figure3agivesaschematicrepresentationofthedecoderarchitec-ture.3.2EncodersNotethatwithouttheencodertermthisrepresentsastandardlanguagemodel.Byincorporatinginencandtrainingthetwoelementsjointlywecru-ciallycanincorporatetheinputtextintogenera-tion.Wediscussnextseveralpossibleinstantia-tionsoftheencoder.Bag-of-WordsEncoderOurmostbasicmodelsimplyusesthebag-of-wordsoftheinputsentenceembeddeddowntosizeH,whileignoringproper-tiesoftheoriginalorderorrelationshipsbetweenneighboringwords.Wewritethismodelas:enc1(x,yc)=p>˜x,p=[1/M,...,1/M],˜x=[Fx1,...,FxM].Wheretheinput-sideembeddingmatrixF∈RH×Vistheonlynewparameteroftheencoder

5it [01:50, 22.04s/it]

Wall time: 45min 14s
